## Inżynieria uczenia maszynowego
### 22 maja 2024
# 10. DVC

<img src="img/expcontrol/dvc-logo.png">

## DVC - Data Version Control
- [dvc.org](https://dvc.org/)
- "Version Control System for Machine Learning Projects" (System kontroli wersji dla projektów uczenia maszynowego)
- Open Source
- Umożliwia:
  - wersjonowanie danych i modeli. "Git dla danych i modeli"
  - budowanie potoków ("pipeline") definiujących jak budować/trenować/ewaluować modele. "Makefile dla uczenia maszynowego"
  - śledzenie, porównywanie metryk i parametrów
- ściśle zintegowany z gitem
- działa niezależnie od używanego języka/bibliotek i systemu operacyjnego
- 5-minutowe wprowadzenie: https://www.youtube.com/watch?v=UbL7VUpv1Bs

## Śledzenie plików za pomocą DVC
 - dużymi plikami, takimi jak plikami z danymi wejściowymi czy plikami modeli, trudno zarządza się za pomocą gita, ze względu na problemy z:
   - wydajnością
   - przestrzenią w repozytorium
   - ograniczenia ze strony serwisu (np. [limit 100 MB na plik w Github](https://docs.github.com/en/repositories/working-with-files/managing-large-files/about-large-files-on-github))
 - Git posiada rozszerzenie [lfs(Large File Storage)](https://git-lfs.github.com/), które stanowi pewne rozwiązanie tego problemu. 
   - Same pliki przechowywane są na specjalnym zdalnym serwerze, w repozytorium przechowywane są jedynie odnośniki do tych plików i pewne metadane
   - Github ma zintegrowany LFS z [limitem 1GB dla kont bezpłatnych](https://docs.github.com/en/repositories/working-with-files/managing-large-files/about-storage-and-bandwidth-usage)

 - DVC proponuje podobne podejście co LFS, ale:
   - pliki mogą być przechowywane na niemal dowolnym serwerze, również lokalnie
   - brak limitu wielkości plików (w Git-LFS na Github [limit 2GB](https://docs.github.com/en/repositories/working-with-files/managing-large-files/about-git-large-file-storage))
   - DVC zapewnia dodatkowe narzędzie umożliwiające śledzenie plików i ich powiązań z  wynikami eksperymentów
   - więcej, patrz [tutaj](https://dvc.org/doc/user-guide/related-technologies)

## Instalacja i inicjalizacja
 - https://dvc.org/doc/install
 - ```pip install dvc```
 - ```pipx install dvc```
 - ```conda install dvc```

In [1]:
!pip3 install dvc

Stwórzmy katalog, w którym będziemy przechowywać nasz projekt:

In [4]:
!rm -r -f IUM_10/sample-ml-project-2024
!mkdir -p IUM_10/sample-ml-project-2024

In [5]:
#Jupyter notebook magic https://ipython.readthedocs.io/en/stable/interactive/magics.html#magic-cd
%cd "IUM_10/sample-ml-project-2024"

/home/pawel/ium/IUM_10/sample-ml-project-2024


/home/pawel/ium/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


Inicjalizujemy puste repozytorium Git (możemy też pominąć ten krok i działać w istniejącym już repozytorium)

In [7]:
!git init

Reinitialized existing Git repository in /home/pawel/ium/IUM_10/sample-ml-project-2024/.git/


Teraz inicjalizujemy repozytorium DVC:

In [8]:
!dvc init

Initialized DVC repository.

You can now commit the changes to git.

+---------------------------------------------------------------------+
|                                                                     |
|        DVC has enabled anonymous aggregate usage analytics.         |
|     Read the analytics documentation (and how to opt-out) here:     |
|             <https://dvc.org/doc/user-guide/analytics>              |
|                                                                     |
+---------------------------------------------------------------------+

What's next?
------------
- Check out the documentation: <https://dvc.org/doc>
- Get help and share ideas: <https://dvc.org/chat>
- Star us on GitHub: <https://github.com/iterative/dvc>


Zobaczmy jakie pliki dodał (również do repozytorium git) DVC.
Ich opis znajdziemy tutaj: https://dvc.org/doc/user-guide/project-structure/internal-files

In [9]:
!git status

On branch master

No commits yet

Changes to be committed:
  (use "git rm --cached <file>..." to unstage)
	new file:   .dvc/.gitignore
	new file:   .dvc/config
	new file:   .dvcignore



- `.dvc/config` - główny plik konfiguracyjny DVC
- `.dvc/config.local` - nadpisuje wartości z `config`, do lokalnych zmian niecommitowanych do repozytorium
- `.dvc/.gitignore` - pliki DVC, które nie mają znaleźć się w repo
- `.dvcignore` - DVC pomija pliki zdefiniowane w tym pliku (np. aby poprawić wydajność)

Możemy teraz zacommitować zmiany w git:

In [10]:
!git commit -m "Initial commit"

[master (root-commit) a9746ad] Initial commit
 3 files changed, 6 insertions(+)
 create mode 100644 .dvc/.gitignore
 create mode 100644 .dvc/config
 create mode 100644 .dvcignore


Przygotujmy przykładowe dane, pobierając je z Kaggle:

In [11]:
!kaggle datasets download -d uciml/iris
!unzip -o iris.zip
!rm database.sqlite iris.zip
!mkdir -p data
!mv Iris.csv data/

  0%|                                               | 0.00/3.60k [00:00<?, ?B/s]
100%|██████████████████████████████████████| 3.60k/3.60k [00:00<00:00, 8.23MB/s]
Archive:  iris.zip
  inflating: Iris.csv                
  inflating: database.sqlite         


Teraz dodamy plik(i) z danymi do DVC:

In [12]:
!dvc add data/Iris.csv

⠋ Checking graph                                       core>
Adding...                                                                       
!
                                                                                
!
  0% Checking cache in '/home/pawel/ium/IUM_10/sample-ml-project-2024/.dvc/cache
                                                                                
!
  0%|          |Adding data/Iris.csv to cache         0/1 [00:00<?,     ?file/s]
                                                                                
!
  0%|          |Checking out /home/pawel/ium/IUM_10/sa0/1 [00:00<?,    ?files/s]
100% Adding...|████████████████████████████████████████|1/1 [00:00, 31.90file/s]

To track the changes with git, run:

	git add data/.gitignore data/Iris.csv.dvc

To enable auto staging, run:

	dvc config core.autostage true


 - DVC utworzył plik `data/Iris.csv.dvc` i dodał oryginalny plik do `.gitignore`
 - W repozytorium będzie obecny tylko plik `*.dvc`, zawierający odnośnik do prawdziwego pliku

In [13]:
!git status -u

On branch master
Untracked files:
  (use "git add <file>..." to include in what will be committed)
	data/.gitignore
	data/Iris.csv.dvc

nothing added to commit but untracked files present (use "git add" to track)


Dodajmy pliki `data/Iris.csv.dvc data/.gitignore` do repozytorium git, zgodnie z sugestią DVC:

In [14]:
!git add data/Iris.csv.dvc data/.gitignore

In [15]:
!git commit -m "Dodano dane IRIS (DVC)"

[master 92b2c9d] Dodano dane IRIS (DVC)
 2 files changed, 6 insertions(+)
 create mode 100644 data/.gitignore
 create mode 100644 data/Iris.csv.dvc


Plik `*.dvc` zawiera m.in. hash pliku. Więcej o plikach `*.dvc`: [link](https://dvc.org/doc/user-guide/project-structure/dvc-files)

In [16]:
# %load data/Iris.csv.dvc


Oryginalny plik `Iris.csv` został przeniesiony do katalogu ./dvc/cache/{wartość hash pliku) i podlinkowany z powrotem do oryginalnej lokalizacji. Sposób tworzenia linków może być [różny w zależności od systemu plików](https://dvc.org/doc/user-guide/large-dataset-optimization).

In [18]:
!ls -l .dvc/cache/files/md5/71

total 8
-r--r--r-- 1 pawel pawel 5107 Sep 19  2019 7820ef0af287ff346c5cabfb4c612c


In [19]:
!head -n 3 .dvc/cache/files/md5/71/7820ef0af287ff346c5cabfb4c612c

Id,SepalLengthCm,SepalWidthCm,PetalLengthCm,PetalWidthCm,Species
1,5.1,3.5,1.4,0.2,Iris-setosa
2,4.9,3.0,1.4,0.2,Iris-setosa


## dvc remote
 - Żeby wysłać właściwe pliki śledzone przez DVC do zdalnej lokalizacji (z której będą mogłby być pobrane np. przez system CI albo innych użytkowników), musimy mieć skonfigurowaną taką lokazliację.
 - Służy do tego polecenie [`dvc remote add`](https://dvc.org/doc/command-reference/remote/add).
 - Użyjemy lokalnego "remote". Tutaj będzie to po prostu utworzony wcześniej katalog `/dvcstore`. Taki katalog istnieje też na naszym Jenkinsie, oczywiście należy go podmontować w Dockerze.
 - W rzeczywistych zastosowaniach podalibyśmy tutaj ścieżkę do jakiegoś zasobu dostępnego przez internet jak np. serwer SFTP, ścieżka do AWS S3 itp.

Obsługiwane typy zdalnych lokalizacji (remotes): https://dvc.org/doc/command-reference/remote/add#supported-storage-types
 - Amazon S3
 - S3-compatible storage
 - Microsoft Azure Blob Storage
 - Google Drive
 - Google Cloud Storage
 - Aliyun OSS
 - SSH
 - HDFS
 - WebHDFS
 - HTTP
 - WebDAV
 - local remote

#### Dodawanie remote typu local

In [30]:
!dvc remote add -d my_local_remote ~/dvcstore

Setting 'my_local_remote' as a default remote.


In [31]:
!git status

On branch master
Changes not staged for commit:
  (use "git add <file>..." to update what will be committed)
  (use "git restore <file>..." to discard changes in working directory)
	modified:   .dvc/config

no changes added to commit (use "git add" and/or "git commit -a")


In [32]:
!git add .dvc/config
!git commit -m "Added DVC remote"

[master 7123494] Added DVC remote
 1 file changed, 1 insertion(+), 1 deletion(-)


## dvc push
Kiedy mamy już skonfigurowany "remote" możemy wypchnąć do niego pliki korzystając z polecenia `dvc push`:

In [33]:
!dvc push

Pushing
!
  0% Checking cache in '/home/pawel/dvcstore/files/md5'| |0/? [00:00<?,    ?file
                                                                                
!
  0% Checking cache in '/home/pawel/ium/IUM_10/sample-ml-project-2024/.dvc/cache
                                                                                
!
  0%|          |Pushing to local                      0/1 [00:00<?,     ?file/s]
Pushing                                                                         
1 file pushed


In [35]:
!tree ~/dvcstore

/home/pawel/dvcstore
└── files
    └── md5
        └── 71
            └── 7820ef0af287ff346c5cabfb4c612c

3 directories, 1 file


## dvc pull
Żeby pobrać dane z DVC (np. w innej lokalizacji, przez innego użytkownika), musimy:
 - sklonować repozytorium git (żeby m.in. pobrać pliki `*.dvc`
 - wykonać `dvc pull`

Dodawanie nowych plików i modyfikacja istniejących wygląda podobnie jak przy zwykłych plikach śledzonych przez  git, tylko zamiast `git` używamy polecenia `dvc` a dodatkowo pamiętamy o zarządzaniu plikami `*.dvc` za pomocą gita:

In [37]:
!head -n -1 data/Iris.csv | tee data/Iris.csv

Id,SepalLengthCm,SepalWidthCm,PetalLengthCm,PetalWidthCm,Species
1,5.1,3.5,1.4,0.2,Iris-setosa
2,4.9,3.0,1.4,0.2,Iris-setosa
3,4.7,3.2,1.3,0.2,Iris-setosa
4,4.6,3.1,1.5,0.2,Iris-setosa
5,5.0,3.6,1.4,0.2,Iris-setosa
6,5.4,3.9,1.7,0.4,Iris-setosa
7,4.6,3.4,1.4,0.3,Iris-setosa
8,5.0,3.4,1.5,0.2,Iris-setosa
9,4.4,2.9,1.4,0.2,Iris-setosa
10,4.9,3.1,1.5,0.1,Iris-setosa
11,5.4,3.7,1.5,0.2,Iris-setosa
12,4.8,3.4,1.6,0.2,Iris-setosa
13,4.8,3.0,1.4,0.1,Iris-setosa
14,4.3,3.0,1.1,0.1,Iris-setosa
15,5.8,4.0,1.2,0.2,Iris-setosa
16,5.7,4.4,1.5,0.4,Iris-setosa
17,5.4,3.9,1.3,0.4,Iris-setosa
18,5.1,3.5,1.4,0.3,Iris-setosa
19,5.7,3.8,1.7,0.3,Iris-setosa
20,5.1,3.8,1.5,0.3,Iris-setosa
21,5.4,3.4,1.7,0.2,Iris-setosa
22,5.1,3.7,1.5,0.4,Iris-setosa
23,4.6,3.6,1.0,0.2,Iris-setosa
24,5.1,3.3,1.7,0.5,Iris-setosa
25,4.8,3.4,1.9,0.2,Iris-setosa
26,5.0,3.0,1.6,0.2,Iris-setosa
27,5.0,3.4,1.6,0.4,Iris-setosa
28,5.2,3.5,1.5,0.2,Iris-setosa
29,5.2,3.4,1.4,0.2,Iris-setosa
30,4.7,3.2,1.6,0.2,Iris-setosa
31,4.8,3.1,1.6

In [38]:
!git status

On branch master
nothing to commit, working tree clean


In [39]:
!dvc status

data/Iris.csv.dvc:                                                              
	changed outs:
		modified:           data/Iris.csv


In [40]:
!dvc add data/Iris.csv

⠋ Checking graph                                       core>
Adding...                                                                       
!
                                                                                
!
  0% Checking cache in '/home/pawel/ium/IUM_10/sample-ml-project-2024/.dvc/cache
                                                                                
!
  0%|          |Adding data/Iris.csv to cache         0/1 [00:00<?,     ?file/s]
                                                                                
!
  0%|          |Checking out /home/pawel/ium/IUM_10/sa0/1 [00:00<?,    ?files/s]
100% Adding...|████████████████████████████████████████|1/1 [00:00, 50.81file/s]

To track the changes with git, run:

	git add data/Iris.csv.dvc

To enable auto staging, run:

	dvc config core.autostage true


In [41]:
!git add data/Iris.csv.dvc
!git commit -m "Removed last line from Iris dataset"


[master 9de24e1] Removed last line from Iris dataset
 1 file changed, 2 insertions(+), 2 deletions(-)


In [43]:
!wc -l .dvc/cache/files/md5/*/*

  151 .dvc/cache/files/md5/71/7820ef0af287ff346c5cabfb4c612c
  150 .dvc/cache/files/md5/bc/cff2e578d76852294184c1dce9fdbf
  301 total


### dvc checkout
  - Polecenia `dvc checkout` używamy razem z `git checkout`, żeby zmienić gałąź, na której pracujemy.
  - DVC podmieni wersje plików śledzonych przez siebie na pochodzące z innej gałęzi (o ile pliki te się różnią i różnią się pliki `*.dvc` na odpowiednich gałęziach)
  - Zmiana gałęzi przez git powoduje (ewentualną) zmianę plików `*.dvc` a `dvc checkout` kopiuje/linkuje pliki z katalogu `.dvc/cache` o wartościach hash odpowiadających tym z plików `*.dvc`.

## Wymiana danych między projektami
 - za pomocą poleceń `dvc import` i `dvc update` możemy dodać i później aktualizować pliki śledzone przez DVC w innym repozytorium

In [44]:
!dvc import https://github.com/iterative/dataset-registry \
             get-started/data.xml -o data/data.xml

Importing 'get-started/data.xml (https://github.com/iterative/dataset-registry)' -> 'data/data.xml'
  0% Downloading data.xml|                           |0/1 [00:00<?,    ?files/s]
!
  0%|          |get-started/data.xml           0.00/13.8M [00:00<?,        ?B/s]
  0%|          |get-started/data.xml      16.5k/13.8M [00:00<01:47,     135kB/s]
  0%|          |get-started/data.xml      66.5k/13.8M [00:00<00:48,     294kB/s]
  1%|          |get-started/data.xml       102k/13.8M [00:00<00:48,     295kB/s]
  2%|▏         |get-started/data.xml       221k/13.8M [00:00<00:25,     566kB/s]
  3%|▎         |get-started/data.xml       374k/13.8M [00:00<00:17,     813kB/s]
  3%|▎         |get-started/data.xml       493k/13.8M [00:00<00:15,     873kB/s]
  5%|▍         |get-started/data.xml       697k/13.8M [00:00<00:12,    1.10MB/s]
  6%|▌         |get-started/data.xml       799k/13.8M [00:01<00:13,    1.02MB/s]
  7%|▋         |get-started/data.xml       935k/13.8M [00:01<00:12,    1.05MB/s]
  8%|▊ 

In [46]:
!dvc status

Data and pipelines are up to date.                                              


In [47]:
ls -l data

total 14124
-rw-r--r-- 1 pawel pawel     5072 May 22 07:57 Iris.csv
-rw-r--r-- 1 pawel pawel       88 May 22 07:57 Iris.csv.dvc
-rw-r--r-- 1 pawel pawel 14445097 May 22 07:59 data.xml
-rw-r--r-- 1 pawel pawel      296 May 22 07:59 data.xml.dvc


## DVC pipelines
 - Wprowadzenie: https://youtu.be/71IGzyH95UY
 - Getting started: https://dvc.org/doc/start/data-pipelines
 - DVC pipelines pozwalają zbudować (za pomocą polecenia `dvc run`) lub zdefiniować (edytując plik `dvc.yaml`) graf zależności między krokami wykonywanymi w naszym projekcie (takimi jak "przygotowanie danych", "uczenie", "ewaluacja").
- Tak zdefiniowany pipeline można potem uruchomić za pomocą polecenia `dvc reproduce`.

## Zadania [10 pkt + dodatkowo 10 pkt]
### Termin: 29 maja 2024
1. Zainicjalizuj repozytorium DVC wewnątrz Twojego repozytorium z projektem [1pkt]
2. Dodaj plik(i) z danymi w Twoim projekcie do DVC [1pkt]
3. Skonfiguruj remote (dane do konfiguracji podane poniżej) [3pkt]
4. [Dodatkowo] Stwórz/zdefiniuj i dodaj do repozytorium plik `dvc.yaml` opisujący kroki wykonywane w Twoim projekcie. Wydziel przynajmniej 2 kroki (np. przygotowanie danych/trenowanie) powiązane ze sobą za pomocą zależności (skorzystaj z 
materiałów "Getting started", link powyżej) [10pkt (opcjonalne)]
5. Stwórz projekt na Jenkinsie (`s1233456-dvc`), w którym sklonujesz repozytorium, ściągniesz pliki dvc (za pomocą `dvc pull`) i uruchomisz pipeline (za pomocą `dvc reproduce`) [5pkt]

## SSH remote
Jednym z remote obsługiwanych przez DVC jest SFTP/SSH.
W celu jego wykorzystania na serwerze tzietkiewicz.vm.wmi.amu.edu.pl utworzony został użytkownik `ium-sftp` i skonfigurowany serwer SFTP.
Został też dla niego wygenerowany klucz ssh, który został dodany jako "Jenkins credential" (patrz opis konfiguracji na Jenkins poniżej)

### Lokalnie
Będziemy potrzebować zależności ([szczegóły](https://dvc.org/doc/command-reference/remote/add))
  
  `conda install dvc-ssh` 

albo

`pip install dvc[ssh] paramiko`

In [50]:
# conda install -c conda-forge dvc-ssh

!pip install dvc[ssh] paramiko

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.9/225.9 KB 4.1 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 283.7/283.7 KB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 856.7/856.7 KB 14.2 MB/s eta 0:00:00a 0:00:01


In [51]:
## Poniższe są potrzebne, żeby polecania dvc remote działały:
!sudo apt install libssl3 libffi7

[sudo] password for pawel: 


Dodajemy remote:

In [52]:
!dvc remote add -f -d ium_ssh_remote ssh://ium-sftp@tzietkiewicz.vm.wmi.amu.edu.pl

Setting 'ium_ssh_remote' as a default remote.


In [53]:
!dvc remote list

my_local_remote	/home/pawel/dvcstore
ium_ssh_remote	ssh://ium-sftp@tzietkiewicz.vm.wmi.amu.edu.pl


Zapisujemy hasło:

In [54]:
!dvc remote modify --local ium_ssh_remote password IUM@2021

Pushujemy do skonfigurowanego remote:

In [55]:
!dvc push

Pushing
!
  0% Checking cache in 'files/md5'|                  |0/? [00:00<?,    ?files/s]
                                                                                
!
  0% Checking cache in '/home/pawel/ium/IUM_10/sample-ml-project-2024/.dvc/cache
                                                                                
!
  0%|          |Pushing to ssh                        0/1 [00:00<?,     ?file/s]

!

  0%|          |/home/pawel/ium/IUM_10/sample-m0.00/4.95k [00:00<?,        ?B/s]

                                                                                
100%|██████████|Pushing to ssh                    1/1 [00:00<00:00,  8.63file/s]
Pushing                                                                         
1 file pushed


### Jenkins

W Jenkins można użyć mechanizmu "Credentials", żeby w bezpieczny sposób przekazać hasło albo klucz prywatny.

Takie dane dla użytkownika ium-sftp zostały stworzone na Jenkinsie:

 - typu ssh key: https://tzietkiewicz.vm.wmi.amu.edu.pl:8081/credentials/store/system/domain/_/credential/48ac7004-216e-4260-abba-1fe5db753e18/
 - typu "secret text" - zawierający hasło użytkownika ium-shftp: https://tzietkiewicz.vm.wmi.amu.edu.pl:8081/credentials/store/system/domain/_/credential/ium-sftp-password/

Opis używania "Credentials" w Jenkinsfile: https://www.jenkins.io/doc/book/pipeline/jenkinsfile/#for-other-credential-types

Klucza ssh można użyć tak: 

```Jenkinsfile
withCredentials(
    [sshUserPrivateKey(credentialsId: '48ac7004-216e-4260-abba-1fe5db753e18', keyFileVariable: 'IUM_SFTP_KEY', passphraseVariable: '', usernameVariable: '')]) {
                sh 'dvc remote add -d ium_ssh_remote ssh://ium-sftp@tzietkiewicz.vm.wmi.amu.edu.pl/ium-sftp'
                sh 'dvc remote modify --local ium_ssh_remote keyfile $IUM_SFTP_KEY'
                sh 'dvc pull'}
```

Secret text tak:

```Jenkinsfile
    withCredentials([string(credentialsId: 'ium-sftp-password', variable: 'IUM_SFTP_PASS')]) {
                sh 'dvc remote add -d ium_ssh_remote ssh://ium-sftp@tzietkiewicz.vm.wmi.amu.edu.pl/ium-sftp'
                sh 'dvc remote modify --local ium_ssh_remote password $IUM_SFTP_PASS'
                sh 'dvc pull'
    }
```

Przykład konfiguracji: 
 - https://tzietkiewicz.vm.wmi.amu.edu.pl:8081/job/docker-test-mount/ 
 - https://git.wmi.amu.edu.pl/tzietkiewicz/ium-helloworld